<a href="https://colab.research.google.com/github/patal-dev/april/blob/main/FnV_Experiment.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [1]:
%matplotlib inline

import logging
logging.getLogger('googleapiclient.discovery_cache').setLevel(logging.ERROR)

# Code to read csv file into Colaboratory:
!pip install -U -q PyDrive
from pydrive.auth import GoogleAuth
from pydrive.drive import GoogleDrive
from google.colab import auth
from oauth2client.client import GoogleCredentials
# Authenticate and create the PyDrive client.
auth.authenticate_user()
gauth = GoogleAuth()
gauth.credentials = GoogleCredentials.get_application_default()
drive = GoogleDrive(gauth)
link = 'https://drive.google.com/open?id=1XcFFQS1ZoUOPs9vSJcA_o-Z1rvxi1Kod'
fluff, id = link.split('=')

downloaded = drive.CreateFile({'id':id}) 
downloaded.GetContentFile('wiki.mat')

## Data



*   dob: date of birth (Matlab serial date number)
*photo_taken: year when the photo was taken
*full_path: path to file
*gender: 0 for female and 1 for male, NaN if unknown
*name: name of the celebrity
*face_location: location of the face. 
*face_score: detector score (the higher the better). Inf implies that no face was found in the image and the face_location then just returns the entire image
*second_face_score: detector score of the face with the second highest score. This is useful to ignore images with more than one face. second_face_score is NaN if no second face was detected.
*celeb_names (IMDB only): list of all celebrity names
*celeb_id (IMDB only): index of celebrity name



In [22]:
import scipy.io
import numpy as np

mat = scipy.io.loadmat('wiki.mat')
fields = ('dob', 'photo_taken', 'full_path', 'gender', 'name', 
          'face_location', 'face_score', 'second_face_score')


l = 62328
data = np.empty((0, l))
for i, field in enumerate(fields):
  values = np.array([])
  if field == 'face_location':
    data = np.append(data, [np.empty(l)], axis=0)
    continue
  elif field == 'name':
    values = mat['wiki'][0][0][i].flatten()
  else:
    values = np.hstack(mat['wiki'][0][0][i].flatten())
  data = np.append(data, [values], axis=0)



```
# length = 4
# [1, None, 2, None]
# [1, 2]
```



In [23]:
import pandas as pd

print(data.shape)
df = pd.DataFrame(data).transpose()
df.columns = fields

df

(8, 62328)


dob photo_taken                        full_path gender  \
0      723671.0      2009.0  17/10000217_1981-05-05_2009.jpg    1.0   
1      703186.0      1964.0  48/10000548_1925-04-04_1964.jpg    1.0   
2      711677.0      2008.0    12/100012_1948-07-03_2008.jpg    1.0   
3      705061.0      1961.0  65/10001965_1930-05-23_1961.jpg    1.0   
4      720044.0      2012.0  16/10002116_1971-05-31_2012.jpg    0.0   
...         ...         ...                              ...    ...   
62323  707582.0      1963.0   49/9996949_1937-04-17_1963.jpg    1.0   
62324  711338.0      1970.0   32/9997032_1947-07-30_1970.jpg    1.0   
62325  720620.0      2013.0   09/9998109_1972-12-27_2013.jpg    1.0   
62326  723893.0      2011.0   00/9999400_1981-12-13_2011.jpg    1.0   
62327  713846.0      2008.0    80/999980_1954-06-11_2008.jpg    0.0   

                         name face_location face_score second_face_score  
0           [Sami Jauhojärvi]           0.0   4.300962               NaN  
1            [Dettmar Cramer]           0.0   2.645639          1.949248  
2               [Marc Okrand]           0.0   4.329329               NaN  
3      [Aleksandar Matanović]           0.0       -inf               NaN  
4              [Diana Damrau]           0.0   3.408442               NaN  
...                       ...           ...        ...               ...  
62323             [Guus Haak]           0.0   4.029268               NaN  
62324         [Nico Rijnders]           0.0       -inf               NaN  
62325     [Michael Wiesinger]           0.0   3.494303               NaN  
62326        [Johann Grugger]           0.0       -inf               NaN  
62327    [Greta Van Susteren]           0.0   5.486917               NaN  

[62328 rows x 8 columns]